In [128]:
import json
# from sqlalchemy import create_engine, Table, Column, Integer, String, MetaData
# import sqlite3
import http.client
import time
import collections

### Create Tables (run once)

In [2]:
data_folder = '../../components/Tools/NASHBoard/Data/'

In [74]:
database = data_folder + 'nba.db'

sqliteCon = sqlite3.connect(database)
cur = sqliteCon.cursor()

engine = create_engine('sqlite:///' + database, echo = True)
meta = MetaData()

# stores player injuries
injuries = Table(
   'injuries', meta, 
   Column('id', Integer, primary_key = True),
   Column('team_name', String), 
   Column('full_name', String),
   Column('primary_position', String),
   Column('comment', String),
   Column('status', String),
   Column('start_date', String),
   Column('player_id', String)
)

schedule = Table()

meta.create_all(engine)

2022-12-08 11:51:08,302 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2022-12-08 11:51:08,306 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("injuries")
2022-12-08 11:51:08,307 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-08 11:51:08,311 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("injuries")
2022-12-08 11:51:08,312 INFO sqlalchemy.engine.Engine [raw sql] ()
2022-12-08 11:51:08,384 INFO sqlalchemy.engine.Engine 
CREATE TABLE injuries (
	id INTEGER NOT NULL, 
	team_name VARCHAR, 
	full_name VARCHAR, 
	primary_position VARCHAR, 
	comment VARCHAR, 
	status VARCHAR, 
	start_date VARCHAR, 
	player_id VARCHAR, 
	PRIMARY KEY (id)
)


2022-12-08 11:51:08,385 INFO sqlalchemy.engine.Engine [no key 0.00949s] ()
2022-12-08 11:51:08,398 INFO sqlalchemy.engine.Engine COMMIT


#### Run the below scripts at the start of every week to update data into database

Connect to sportradar API

In [120]:
# testing API with python
f = open('../api_keys.json')
data = json.load(f)
API_key = data["SportRadar"]
conn
def get_conn():
    global conn 
    conn = http.client.HTTPSConnection("api.sportradar.us")

#### Get INJURIES across league

In [109]:
conn.request("GET", "/nba/trial/v7/en/league/injuries.json?api_key=%s" %API_key)
res = conn.getresponse()
data = res.read()
injury_data = data.decode("utf-8")

CannotSendRequest: Request-sent

In [85]:
# reformat injuries data
injuries_list = []
i = 0
for row in json.loads(injury_data)['teams']:
    team = row['market'] + ' ' + row['name']
    for player in row['players']:
        injured = {}
        injured['id'] = i
        injured['team_name'] = team
        injured.update({k: player[k] for k in ('full_name', 'primary_position','reference')})
        injured.update({k: player['injuries'][0][k] for k in ('comment', 'status','start_date','update_date')})
        injured['player_id'] = injured.pop('reference')
        injuries_list.append(injured)
        i = i + 1
print(injuries_list[:2])

[{'id': 0, 'team_name': 'Washington Wizards', 'full_name': 'Bradley Beal', 'primary_position': 'SG', 'comment': 'Beal will be re-evaluated in a week after suffering a hamstring strain according to Shams Charania of The Athletic.', 'status': 'Out', 'start_date': '2022-12-05', 'update_date': '2022-12-05', 'player_id': '203078'}, {'id': 1, 'team_name': 'Washington Wizards', 'full_name': 'Delon Wright', 'primary_position': 'PG', 'comment': 'The Wizards announced that Wright will be re-evaluated in three weeks.', 'status': 'Out', 'start_date': '2022-10-25', 'update_date': '2022-11-22', 'player_id': '1626153'}]


In [82]:
# store in db
# with sqlite3.connect(database) as con:
#     # Insert each entry from json into the table.
#     injury_keys = list(injuries_list[0].keys())
#     for entry in injuries_list:
#         values = [entry.get(key, None) for key in injury_keys]
#         cmd = """INSERT INTO injuries VALUES(
#                     ?,
#                     ?,
#                     ?,
#                     ?,
#                     ?,
#                     ?,
#                     ?,
#                     ?
#                 );"""
#         con.execute(cmd, values)
#     con.commit()

# store in json
with open(data_folder + 'injuries.json', 'w') as outfile:
    json.dump(injuries_list, outfile)

Get schedule for the whole season

Get Player stats for all games/last week
and calculate Fantasy Score

Get Season Schedules

In [44]:
seasons = ['2019','2020','2021','2022']
season_schedules ={}
for season in seasons:
    conn.request("GET", "/nba/trial/v7/en/games/" + season + "/REG/schedule.json?api_key=%s" %API_key)
    time.sleep(2)
    res = conn.getresponse()
    data = res.read()
    season_schedules[season] = data.decode("utf-8")

In [ ]:
season_schedules['2019']

In [58]:
# create game schedule for each year (done)
for season in seasons[3:]:
    print('season',season)
    games_list = []
    future_games_list = []
    for row in json.loads(season_schedules[season])['games']:
        game = {}
        if row['status'] == 'postponed' or row['status'] == 'cancelled':
            continue
        else:
            game['time_zone'] = row['time_zones']['venue']
            game['network'] = row['broadcasts'][0]['network'] if row.get('broadcasts') else 'missing'
            try:
                game['locale'] = row['broadcasts'][0]['locale']
            except:
                game['locale'] = 'home'
            game['home'] = row['home']['name']
            game['away'] = row['away']['name']
            if row['status'] == 'scheduled':
                game.update({k: row[k] for k in ('id', 'scheduled')})
                future_games_list.append(game)
            else:
                # try:
                game.update({k: row[k] for k in ('id', 'scheduled','home_points','away_points')})
                
                games_list.append(game)
        
    # store in json
    with open(data_folder + 'season_' + season + '_schedule.json', 'w') as outfile:
        json.dump(games_list, outfile)
    if season == '2022':
        with open(data_folder + 'season_' + season + 'remaining_schedule.json', 'w') as outfile:
            json.dump(future_games_list, outfile)

season 2022


In [ ]:
# add weekly game to current season and remove from remaining games
szn = "2022"
conn.request("GET", "/nba/trial/v7/en/games/" + szn + "/REG/schedule.json?api_key=%s" %API_key)
res = conn.getresponse()
data = res.read()
curr_season_schedule = data.decode("utf-8")

Get game box scores for all games played

In [9]:
# load all games
with open(data_folder + 'season_2022_schedule.json', "r") as read_content:
    season_2022 = json.load(read_content)
season_2022_ids = [game['id'] for game in season_2022]
season_2022_ids[:2]

['9f01b268-29c5-4f0e-bf67-21e3dbcf3005',
 'c665e441-9f38-48a7-8796-1f7292f97db1']

In [10]:
len(season_2022_ids)

376

In [159]:
# get teeam ids
get_conn()
conn.request("GET", '/nba/trial/v7/en/league/hierarchy.json?api_key=%s' %API_key)
res = conn.getresponse()
data = res.read()
team_info = data.decode("utf-8")

In [163]:
# add id to team json
def flat(l):
  return [y for x in l for y in x]
# team_info = json.loads(team_info)
divisions = flat([c['divisions'] for c in team_info['conferences']])
flat([t2['teams'] for t2 in divisions])
team_id_dict = {t['market'] + ' ' + t['name']:t['id'] for t in flat([t2['teams'] for t2 in divisions])}
od = collections.OrderedDict(sorted(team_id_dict.items()))

[{'id': '583ec8d4-fb46-11e1-82cb-f4ce4684ea4c',
  'name': 'Wizards',
  'market': 'Washington',
  'alias': 'WAS',
  'sr_id': 'sr:team:3431',
  'reference': '1610612764',
  'venue': {'id': 'f62d5b49-d646-56e9-ba60-a875a00830f8',
   'name': 'Capital One Arena',
   'capacity': 20356,
   'address': '601 F Street NW',
   'city': 'Washington',
   'state': 'DC',
   'zip': '20004',
   'country': 'USA',
   'sr_id': 'sr:venue:6016'}},
 {'id': '583ec97e-fb46-11e1-82cb-f4ce4684ea4c',
  'name': 'Hornets',
  'market': 'Charlotte',
  'alias': 'CHA',
  'sr_id': 'sr:team:3430',
  'reference': '1610612766',
  'venue': {'id': 'a380f011-6e5d-5430-9f37-209e1e8a9b6f',
   'name': 'Spectrum Center',
   'capacity': 19077,
   'address': '330 E. Trade Street',
   'city': 'Charlotte',
   'state': 'NC',
   'zip': '28202',
   'country': 'USA',
   'sr_id': 'sr:venue:6146'}},
 {'id': '583ecb8f-fb46-11e1-82cb-f4ce4684ea4c',
  'name': 'Hawks',
  'market': 'Atlanta',
  'alias': 'ATL',
  'sr_id': 'sr:team:3423',
  'refere

In [139]:
# save team ids in team json
with open(data_folder + 'teams.json', "r") as read_content:
    team_json = json.load(read_content)
for i,team in enumerate(team_json):
    team['sr-id'] = od[list(od.keys())[i]]
with open(data_folder + 'teams.json', 'w') as outfile:
    json.dump(team_json, outfile)

get team rosters --> get sr-ids for each player

In [175]:
team_sr_ids = [t['sr-id'] for t in team_json]
get_conn()
player_sr_id_dict = {}
for t in team_sr_ids:
    time.sleep(1)
    conn.request("GET", "/nba/trial/v7/en/teams/" + t + "/profile.json?api_key=%s" %API_key)
    res = conn.getresponse()
    data = res.read()
    team_profile = json.loads(data.decode("utf-8"))
    player_sr_id_dict.update({t['full_name']:t['id'] for t in team_profile['players']})

In [177]:
# player_sr_id_dict
with open(data_folder + 'players.json', 'w') as outfile:
    json.dump(player_sr_id_dict, outfile)

In [121]:
# for id in season_2022_ids:
# id = season_2022_ids[0]
season = '2022'
team_id = list(team_id_dict.values())[0]
# team_id
# conn.request("GET", "/nba/trial/v7/en/games/"+id+"/boxscore.json?api_key=%s" %API_key)
conn.request("GET", "/nba/trial/v7/en/seasons/" + season + "/REG/teams/" + team_id + "/splits/game.json?api_key=%s" %API_key)
res = conn.getresponse()
data = res.read()
sample_team_splits = data.decode("utf-8")
sample_team_splits = json.loads(sample_team_splits)

In [ ]:
sample_team_splits['splits'][0].keys()

get player splits for each game

get player splits for season

In [216]:
get_conn()
# p_id = list(player_sr_id_dict.values())[0]
i = 0
players_splits = {}
for p_name, p_id in player_sr_id_dict.items():
    time.sleep(1)
    if i % 25 == 0:
        print(p_name, p_id)
    conn.request("GET","/nba/trial/v7/en/players/"+p_id+"/profile.json?api_key=%s"%API_key)
    res = conn.getresponse()
    data = res.read()
    player = data.decode("utf-8")
    player = json.loads(player)
    season_stats = player['seasons']
    player_dict = {s['year']: {'team':s['teams'][0]['market'] +' ' + s['teams'][0]['name'], 'total':s['teams'][0]['total'],'average':s['teams'][0]['average'] } for s in season_stats}
    players_splits[p_name] = player_dict
    i= i + 1

Justin Holiday 05dea31d-f1ff-491b-9f17-8be88b26f413
Derrick White 9bcd5cff-4a1c-4454-89b6-a5899b0c6bcc
Kai Jones 116f036d-9233-462b-80bc-3ede69b97706
Malcolm Hill 787f64f8-b127-47da-b05b-6b4324a502a0
Tim Hardaway Jr. 35cd1338-c56b-4247-b53c-264585c59883
Bones Hyland 7ad01370-ae8e-40ae-b70d-61f6d8dba8d9
Patrick Baldwin Jr. 003883ca-cd7e-4b58-99d7-6fef54afdfeb
Josh Christopher 8121242f-45a6-4632-b8ae-f0846a45016a
Ivica Zubac 2da18268-82d4-4b40-a296-7ceddd435d0b
Cole Swider cae1e67f-229e-46c8-851a-571d728ae315
Bam Adebayo 11c303dc-540c-4090-8e0c-76c2fb2c125a
Wesley Matthews 795bcca3-0cca-448c-8198-85c664f76c75
Dereon Seabron 1ad3d938-c2af-4567-b968-95dd79427fa5
Svi Mykhailiuk 8c0929ae-ce3d-47e0-a964-bf6b8d3981ab
Chet Holmgren eb91a4c8-1a8a-46bf-86e6-e16950b67ef6
Matisse Thybulle 8b43c272-c16b-40c7-a4d5-7bbcefeb1816
Greg Brown III 03258eec-a666-4b8f-86da-9bed8e91c39f
KZ Okpala 77dc9e11-c422-4c1b-9545-0f487095891e
Khem Birch 13ef372a-5fd1-4336-9901-12e120a5fbd7
Walker Kessler 7eccbdf9-58a3-

In [217]:
players_splits

{'Justin Holiday': {2022: {'team': 'Atlanta Hawks',
   'total': {'games_played': 20,
    'games_started': 0,
    'minutes': 338.0,
    'field_goals_made': 41,
    'field_goals_att': 105,
    'field_goals_pct': 0.39,
    'two_points_made': 16,
    'two_points_att': 33,
    'two_points_pct': 0.485,
    'three_points_made': 25,
    'three_points_att': 72,
    'three_points_pct': 0.347,
    'blocked_att': 3,
    'free_throws_made': 0,
    'free_throws_att': 0,
    'free_throws_pct': 0.0,
    'offensive_rebounds': 1,
    'defensive_rebounds': 18,
    'rebounds': 19,
    'assists': 17,
    'turnovers': 12,
    'assists_turnover_ratio': 1.42,
    'steals': 5,
    'blocks': 7,
    'personal_fouls': 32,
    'tech_fouls': 0,
    'points': 107,
    'flagrant_fouls': 0,
    'ejections': 0,
    'foulouts': 0,
    'true_shooting_att': 105.0,
    'true_shooting_pct': 0.51,
    'efficiency': 79,
    'points_off_turnovers': 18,
    'points_in_paint': 24,
    'points_in_paint_made': 12,
    'points_in_p

In [218]:
with open(data_folder + 'player_splits.json', 'w') as outfile:
    json.dump(players_splits, outfile)
# players_splits

In [211]:
sample_player.keys()
season_stats = sample_player['seasons']
# season_stats[0]['teams'][0].keys()
# season_stats[0]['teams'][0]['total']
season_stats[0]['teams'][0]['average']
season_stats[2]
{s['year']: {'team':s['teams'][0]['market'] +' ' + s['teams'][0]['name'], 'total':s['teams'][0]['total'],'average':s['teams'][0]['average'] } for s in season_stats}
# [s for s in season_stats['teams']]

{2022: {'team': 'Atlanta Hawks',
  'total': {'games_played': 20,
   'games_started': 0,
   'minutes': 338.0,
   'field_goals_made': 41,
   'field_goals_att': 105,
   'field_goals_pct': 0.39,
   'two_points_made': 16,
   'two_points_att': 33,
   'two_points_pct': 0.485,
   'three_points_made': 25,
   'three_points_att': 72,
   'three_points_pct': 0.347,
   'blocked_att': 3,
   'free_throws_made': 0,
   'free_throws_att': 0,
   'free_throws_pct': 0.0,
   'offensive_rebounds': 1,
   'defensive_rebounds': 18,
   'rebounds': 19,
   'assists': 17,
   'turnovers': 12,
   'assists_turnover_ratio': 1.42,
   'steals': 5,
   'blocks': 7,
   'personal_fouls': 32,
   'tech_fouls': 0,
   'points': 107,
   'flagrant_fouls': 0,
   'ejections': 0,
   'foulouts': 0,
   'true_shooting_att': 105.0,
   'true_shooting_pct': 0.51,
   'efficiency': 79,
   'points_off_turnovers': 18,
   'points_in_paint': 24,
   'points_in_paint_made': 12,
   'points_in_paint_att': 19,
   'points_in_paint_pct': 0.632,
   'effe

In [49]:
# sample_data = json.loads(sample_data)
print(sample_data.keys())
# game_info = {}
# game_info.update({k: row.get(k) for k in ('lead_changes', 'times_tied')})
# sample_data.get('home').get('leaders').keys()
sample_data.get('entry_mode')
# sample_data[0]['id']


dict_keys(['id', 'status', 'coverage', 'scheduled', 'duration', 'attendance', 'lead_changes', 'times_tied', 'clock', 'quarter', 'track_on_court', 'reference', 'entry_mode', 'sr_id', 'clock_decimal', 'time_zones', 'home', 'away'])


'WEBSOCKET'

Get box scores for weeks games

In [ ]:
# load weeks games 


In [ ]:
conn.request("GET", "/nba/trial/v7/en/games/1af034f5-e46e-4b8a-9c82-f91b41f6098e/boxscore.xml?api_key={your_api_key}")

res = conn.getresponse()
data = res.read()

print(data.decode("utf-8"))